In [1]:
import sys, pandas_profiling
import numpy as np, pandas as pd
import matplotlib.pyplot as plt, seaborn as sns
import plotly.graph_objects as go

from collections import OrderedDict
np.set_printoptions(suppress=True, threshold=sys.maxsize)

In [ ]:
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'

In [2]:
%matplotlib inline
pd.set_option("display.max_columns", 100)
pd.set_option('display.max_rows', 1000)
pd.options.display.float_format = '{:.2f}'.format

In [4]:
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.preprocessing import StandardScaler, RobustScaler, MinMaxScaler, LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.neighbors import KNeighborsRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import AdaBoostRegressor, GradientBoostingRegressor, RandomForestRegressor

In [5]:
dataset_hourly = pd.read_csv('dataset_formatted.csv', index_col=0)
dataset_hourly.shape

(127470, 12)

In [6]:
dataset_hourly.head()

Date Clock_Time  Temperature            Weather  Wind_Speed  Humidity  \
0  09-Sep-09       0:40        30.00              Haze.       15.00      0.75   
1  09-Sep-09       1:40        30.00              Haze.       17.00      0.75   
2  09-Sep-09      11:40        31.00  Scattered clouds.       17.00      0.70   
3  09-Sep-09      13:40        33.00             Clear.       19.00      0.59   
4  09-Sep-09      14:40        34.00             Clear.       17.00      0.56   

   Visibility       Formatted_Date  Year  Month  Day Weather_Category  
0        4.00  2009-09-09 00:30:00  2009      9    9            Foggy  
1        4.00  2009-09-09 01:30:00  2009      9    9            Foggy  
2        6.00  2009-09-09 11:30:00  2009      9    9           Cloudy  
3        6.00  2009-09-09 13:30:00  2009      9    9            Clear  
4        6.00  2009-09-09 14:30:00  2009      9    9            Clear

In [7]:
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = pd.DataFrame(data)
    cols, names = list(), list()
    
    column_names = data.columns
    
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('%s(t-%d)' % (column_names[j], i)) for j in range(n_vars)]
    
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('%s(t)' % column_names[j]) for j in range(n_vars)]
        else:
            names += [('%s(t+%d)' % (column_names[j], i) for j in range(n_vars))]
    
    # put it all together
    agg = pd.concat(cols, axis=1)
    agg.columns = names
    
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    
    return agg



In [8]:
dataset_hourly.head()

Date Clock_Time  Temperature            Weather  Wind_Speed  Humidity  \
0  09-Sep-09       0:40        30.00              Haze.       15.00      0.75   
1  09-Sep-09       1:40        30.00              Haze.       17.00      0.75   
2  09-Sep-09      11:40        31.00  Scattered clouds.       17.00      0.70   
3  09-Sep-09      13:40        33.00             Clear.       19.00      0.59   
4  09-Sep-09      14:40        34.00             Clear.       17.00      0.56   

   Visibility       Formatted_Date  Year  Month  Day Weather_Category  
0        4.00  2009-09-09 00:30:00  2009      9    9            Foggy  
1        4.00  2009-09-09 01:30:00  2009      9    9            Foggy  
2        6.00  2009-09-09 11:30:00  2009      9    9           Cloudy  
3        6.00  2009-09-09 13:30:00  2009      9    9            Clear  
4        6.00  2009-09-09 14:30:00  2009      9    9            Clear

In [9]:
reqd_df = dataset_hourly[(~dataset_hourly.Year.isin([2019, 2020])) & (dataset_hourly.Wind_Speed < 20)][
    ['Temperature', 'Humidity', 'Visibility', 'Weather_Category', 'Wind_Speed']].copy()

In [10]:
encoder = LabelEncoder()
reqd_df['Weather_Category'] = encoder.fit_transform(reqd_df['Weather_Category'])

In [11]:
n_sup_df = series_to_supervised(data=reqd_df,
                     n_in=30,
                     n_out=1)

In [12]:
n_sup_df.head()

Temperature(t-30)  Humidity(t-30)  Visibility(t-30)  \
30              30.00            0.75              4.00   
31              30.00            0.75              4.00   
32              31.00            0.70              6.00   
33              33.00            0.59              6.00   
34              34.00            0.56              6.00   

    Weather_Category(t-30)  Wind_Speed(t-30)  Temperature(t-29)  \
30                    2.00             15.00              30.00   
31                    2.00             17.00              31.00   
32                    1.00             17.00              33.00   
33                    0.00             19.00              34.00   
34                    0.00             17.00              35.00   

    Humidity(t-29)  Visibility(t-29)  Weather_Category(t-29)  \
30            0.75              4.00                    2.00   
31            0.70              6.00                    1.00   
32            0.59              6.00                    0.00   
33            0.56              6.00                    0.00   
34            0.53              6.00                    0.00   

    Wind_Speed(t-29)  Temperature(t-28)  Humidity(t-28)  Visibility(t-28)  \
30             17.00              31.00            0.70              6.00   
31             17.00              33.00            0.59              6.00   
32             19.00              34.00            0.56              6.00   
33             17.00              35.00            0.53              6.00   
34             19.00              35.00            0.56              6.00   

    Weather_Category(t-28)  Wind_Speed(t-28)  Temperature(t-27)  \
30                    1.00             17.00              33.00   
31                    0.00             19.00              34.00   
32                    0.00             17.00              35.00   
33                    0.00             19.00              35.00   
34                    1.00             17.00              29.00   

    Humidity(t-27)  Visibility(t-27)  Weather_Category(t-27)  \
30            0.59              6.00                    0.00   
31            0.56              6.00                    0.00   
32            0.53              6.00                    0.00   
33            0.56              6.00                    1.00   
34            0.66              4.00                    2.00   

    Wind_Speed(t-27)  Temperature(t-26)  Humidity(t-26)  Visibility(t-26)  \
30             19.00              34.00            0.56              6.00   
31             17.00              35.00            0.53              6.00   
32             19.00              35.00            0.56              6.00   
33             17.00              29.00            0.66              4.00   
34             15.00              28.00            0.74              4.00   

    Weather_Category(t-26)  Wind_Speed(t-26)  Temperature(t-25)  \
30                    0.00             17.00              35.00   
31                    0.00             19.00              35.00   
32                    1.00             17.00              29.00   
33                    2.00             15.00              28.00   
34                    2.00             11.00              27.00   

    Humidity(t-25)  Visibility(t-25)  Weather_Category(t-25)  \
30            0.53              6.00                    0.00   
31            0.56              6.00                    1.00   
32            0.66              4.00                    2.00   
33            0.74              4.00                    2.00   
34            0.79              4.00                    2.00   

    Wind_Speed(t-25)  Temperature(t-24)  Humidity(t-24)  Visibility(t-24)  \
30             19.00              35.00            0.56              6.00   
31             17.00              29.00            0.66              4.00   
32             15.00              28.00            0.74              4.00   
33             11.00              27.00            

In [13]:
n_sup_df.shape

(100147, 155)

In [14]:
X_columns = n_sup_df.columns.drop(['Temperature(t)', 'Humidity(t)', 'Visibility(t)', 
                                   'Weather_Category(t)', 'Wind_Speed(t)'])
label = 'Wind_Speed(t)'

In [15]:
def X_y(dataset, columns_of_interest, label):
    print(f"Shape of dataset: {dataset.shape}")
    dataset = dataset[pd.notnull(dataset[label])]
    X = dataset[columns_of_interest]
    y = dataset[label]
    print(f"X.shape: {X.shape}, y.shape: {y.shape}")
    return X, y

In [16]:
X, y = X_y(dataset=n_sup_df.copy(), 
           columns_of_interest=X_columns,
           label=label)

Shape of dataset: (100147, 155)
X.shape: (100147, 150), y.shape: (100147,)


In [18]:
SCALERS = [
    None,
#     StandardScaler(),
#     RobustScaler(),
#     MinMaxScaler()
]
REGRESSORS = [
    LinearRegression(),
#     DecisionTreeRegressor(),
#     AdaBoostRegressor(),
#     GradientBoostingRegressor(),
#     RandomForestRegressor()
]

In [19]:
def run_all_models(X, y):
    import warnings; warnings.filterwarnings(action='ignore')
    
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=False)
    print(f"X_train.shape: {X_train.shape}, y_train.shape: {y_train.shape}, X_test.shape: {X_test.shape}, y_test.shape: {y_test.shape}")
    
    cv_scores_df = pd.DataFrame()
    all_pipes = OrderedDict()
        
    for scaler in SCALERS:
        print("\n\n****************************************************************************************")
        print(f"Current Scaler: {scaler.__class__.__name__}")
        print("****************************************************************************************")
        
        cv_scores_dict, cost_estimations_dict  = OrderedDict(), OrderedDict()
        all_pipes[scaler.__class__.__name__] = {}
        
        for regressor in REGRESSORS:
            print("\n****************************************************************************************")
            print(f"Current Regressor: {regressor.__class__.__name__}")
            pipe = Pipeline(
                steps=[('scaler', scaler),
                       ('regressor', regressor)])
            pipe.fit(X_train, y_train)            
            
            y_predicted = pipe.predict(X_test)
            # print(y_predicted)
            print(f"Test MAE: {mean_absolute_error(y_true=y_test, y_pred=y_predicted):.2f}")
            print(f"Test MSE: {mean_squared_error(y_true=y_test, y_pred=y_predicted):.2f}")
            
            cross_val_scores = cross_val_score(estimator=pipe, 
                                               X=X_train, 
                                               y=y_train, 
                                               cv=3,
                                               scoring='r2')
            print(f"3 fold cross validation scores {cross_val_scores}")
            print(f"Mean CV R2: {cross_val_scores.mean():.2f}\n")
            
            all_pipes[scaler.__class__.__name__][regressor.__class__.__name__] = pipe
            cv_scores_dict[regressor.__class__.__name__] = cross_val_scores.mean()
                        
        cv_scores_df = cv_scores_df.append(pd.DataFrame(cv_scores_dict, index = [scaler.__class__.__name__]))
        print("****************************************************************************************")

    return cv_scores_df, all_pipes


In [20]:
#%%time
cv_scores_df, all_pipes = run_all_models(
    X=X, 
    y=y)

X_train.shape: (80117, 150), y_train.shape: (80117,), X_test.shape: (20030, 150), y_test.shape: (20030,)


****************************************************************************************
Current Scaler: NoneType
****************************************************************************************

****************************************************************************************
Current Regressor: LinearRegression
Test MAE: 2.03
Test MSE: 7.56
3 fold cross validation scores [0.6525312  0.70638018 0.74019268]
Mean CV R2: 0.70

****************************************************************************************


In [23]:
best_pipe = all_pipes['NoneType']['LinearRegression']

In [27]:
test_df = dataset_hourly[(dataset_hourly.Year.isin([2019, 2020])) & (dataset_hourly.Wind_Speed < 20)][
    ['Formatted_Date', 'Temperature', 'Humidity', 'Visibility', 'Weather_Category', 'Wind_Speed']
].copy().set_index('Formatted_Date')

In [28]:
test_df.shape

(16621, 5)

In [29]:
test_df['Weather_Category'] = encoder.fit_transform(test_df['Weather_Category'])

In [30]:
test_sup_df = series_to_supervised(data=test_df,
                     n_in=30,
                     n_out=1)

In [31]:
test_sup_df.head()

Temperature(t-30)  Humidity(t-30)  Visibility(t-30)  \
Formatted_Date                                                             
2019-01-01 15:00:00              14.00            0.55              4.00   
2019-01-01 15:30:00              13.00            0.55              4.00   
2019-01-01 16:00:00              13.00            0.59              4.00   
2019-01-01 16:30:00              13.00            0.55              4.00   
2019-01-01 17:00:00              12.00            0.54              4.00   

                     Weather_Category(t-30)  Wind_Speed(t-30)  \
Formatted_Date                                                  
2019-01-01 15:00:00                    0.00              0.00   
2019-01-01 15:30:00                    0.00              6.00   
2019-01-01 16:00:00                    0.00              0.00   
2019-01-01 16:30:00                    0.00              0.00   
2019-01-01 17:00:00                    0.00              0.00   

                     Temperature(t-29)  Humidity(t-29)  Visibility(t-29)  \
Formatted_Date                                                             
2019-01-01 15:00:00              13.00            0.55              4.00   
2019-01-01 15:30:00              13.00            0.59              4.00   
2019-01-01 16:00:00              13.00            0.55              4.00   
2019-01-01 16:30:00              12.00            0.54              4.00   
2019-01-01 17:00:00              11.00            0.62              4.00   

                     Weather_Category(t-29)  Wind_Speed(t-29)  \
Formatted_Date                                                  
2019-01-01 15:00:00                    0.00              6.00   
2019-01-01 15:30:00                    0.00              0.00   
2019-01-01 16:00:00                    0.00              0.00   
2019-01-01 16:30:00                    0.00              0.00   
2019-01-01 17:00:00                    0.00              0.00   

                     Temperature(t-28)  Humidity(t-28)  Visibility(t-28)  \
Formatted_Date                                                             
2019-01-01 15:00:00              13.00            0.59              4.00   
2019-01-01 15:30:00              13.00            0.55              4.00   
2019-01-01 16:00:00              12.00            0.54              4.00   
2019-01-01 16:30:00              11.00            0.62              4.00   
2019-01-01 17:00:00              11.00            0.67              4.00   

                     Weather_Category(t-28)  Wind_Speed(t-28)  \
Formatted_Date                                                  
2019-01-01 15:00:00                    0.00              0.00   
2019-01-01 15:30:00                    0.00              0.00   
2019-01-01 16:00:00                    0.00              0.00   
2019-01-01 16:30:00                    0.00              0.00   
2019-01-01 17:00:00                    2.00              0.00   

                     Temperature(t-27)  Humidity(t-27)  Visibility(t-27)  \
Formatted_Date                                                             
2019-01-01 15:00:00              13.00            0.55              4.00   
2019-01-01 15:30:00              12.00            0.54              4.00   
2019-01-01 16:00:00              11.00            0.62              4.00   
2019-01-01 16:30:00              11.00            0.67              4.00   
2019-01-01 17:00:00              11.00            0.62              4.00   

                     Weather_Category(t-27)  Wind_Speed(t-27)  \
Formatted_Date                                                  
2019-01-01 15:00:00                    0.00              0.00   
2019-01-01 15:30:00                    0.00              0.00   
2019-01-01 16:00:00                    0.00              0.00   
2019-01-01 16:30:00                    2.00              0.00   
2019-01-01 17:00:00                    2.00              0.00   

                     Temperature(t-26)  Humidity(t-26)  Visibilit

In [32]:
test_X, test_y = X_y(dataset=test_sup_df.copy(), 
           columns_of_interest=X_columns,
           label=label)

Shape of dataset: (16278, 155)
X.shape: (16278, 150), y.shape: (16278,)


In [34]:
pred_y = best_pipe.predict(test_X)

# Important!

In [121]:
for time_gap in ['0.5H', '3H', '6H', '12H', '1d']:
    lr_pred_y_sampled = pd.Series(pred_y)
    lr_pred_y_sampled.index = pd.to_datetime(test_y.index)
    lr_pred_y_sampled = lr_pred_y_sampled.resample(f'{time_gap}').mean()

    actual_y_sampled = test_y.copy()
    actual_y_sampled.index = pd.to_datetime(test_y.index)
    actual_y_sampled = actual_y_sampled.resample(f'{time_gap}').mean()
    
    lr_pred_y_sampled.dropna(inplace=True)
    actual_y_sampled.dropna(inplace=True)
    
    mae = mean_absolute_error(y_true=actual_y_sampled,
                              y_pred=lr_pred_y_sampled)
    r2 = r2_score(y_true=actual_y_sampled,
                  y_pred=lr_pred_y_sampled)
    
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=actual_y_sampled.index, y=actual_y_sampled, name="Actual",
                             line_color='deepskyblue'))
    fig.add_trace(go.Scatter(x=lr_pred_y_sampled.index, y=lr_pred_y_sampled, name="Predicted",
                             line_color='dimgray'))
    fig.update_layout(title_text=f'LR: {time_gap}: Actual vs Predicted, \tMAE: {mae:.3f}, \tR2: {r2:.3f}',
                      xaxis_rangeslider_visible=True)
    fig.show()

# MLP

In [41]:
from keras.wrappers.scikit_learn import KerasRegressor
from keras.models import Sequential
from keras.layers import Dense, BatchNormalization, Dropout
from keras import backend as K

import tensorflow as tf

Using TensorFlow backend.


In [42]:
K.clear_session()
model = Sequential()

model.add(Dense(200, input_dim=X.shape[1], kernel_initializer='normal', activation='relu'))
model.add(Dropout(0.2))
model.add(BatchNormalization())

model.add(Dense(200, kernel_initializer='normal', activation='relu'))
model.add(Dropout(0.2))
model.add(BatchNormalization())

model.add(Dense(1, kernel_initializer='normal', activation='relu'))

loss = 'mean_absolute_error'
# loss = tf.keras.losses.Huber()
# loss = tf.keras.losses.KLDivergence()
model.compile(loss=loss, optimizer='adam', metrics=['mse', tf.keras.losses.Huber()])

model.summary()






Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 200)               30200     
_________________________________________________________________
dropout_1 (Dropout)          (None, 200)               0         
_________________________________________________________________
batch_normalization_1 (Batch (None, 200)               800       
_________________________________________________________________
dense_2 (Dense)              (None, 200)               40200     
_________________________________________________________________
dropout_2 (Dropout)          (None, 200)               0         
_________________________________________________________________
batch_normalization_2 (Batch (None, 200)               800       
_____________________

In [43]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=False)
print(f"X_train.shape: {X_train.shape}, y_train.shape: {y_train.shape}, X_test.shape: {X_test.shape}, y_test.shape: {y_test.shape}")
    

X_train.shape: (80117, 150), y_train.shape: (80117,), X_test.shape: (20030, 150), y_test.shape: (20030,)


In [44]:
history = model.fit(x=X_train, 
                    y=y_train, 
                    epochs=10, 
                    batch_size=64, 
                    validation_data=(X_test, y_test),
                    verbose=1)

Train on 80117 samples, validate on 20030 samples
Epoch 1/10
80117/80117 [==============================] - 17s 206us/step - loss: 2.7451 - mean_squared_error: 16.2790 - huber_loss: 2.3362 - val_loss: 1.9754 - val_mean_squared_error: 8.5584 - val_huber_loss: 1.6092
Epoch 2/10
80117/80117 [==============================] - 14s 178us/step - loss: 2.3694 - mean_squared_error: 12.5496 - huber_loss: 1.9660 - val_loss: 1.8759 - val_mean_squared_error: 8.3518 - val_huber_loss: 1.5320
Epoch 3/10
80117/80117 [==============================] - 15s 186us/step - loss: 2.3418 - mean_squared_error: 12.3760 - huber_loss: 1.9412 - val_loss: 2.1157 - val_mean_squared_error: 10.2540 - val_huber_loss: 1.7686
Epoch 4/10
80117/80117 [==============================] - 14s 178us/step - loss: 2.3124 - mean_squared_error: 12.2473 - huber_loss: 1.9150 - val_loss: 1.8935 - val_mean_squared_error: 8.4804 - val_huber_loss: 1.5443
Epoch 5/10
80117/80117 [==============================] - 15s 183us/step - loss: 2.29

In [ ]:
mlp_pred_y = np.rint(model.predict(test_X).reshape(test_y.shape))

In [120]:
for time_gap in ['0.5H', '3H', '6H', '12H', '1d']:
    mlp_pred_y_sampled = pd.Series(mlp_pred_y)
    mlp_pred_y_sampled.index = pd.to_datetime(test_y.index)
    mlp_pred_y_sampled = mlp_pred_y_sampled.resample(f'{time_gap}').mean()

    actual_y_sampled = test_y.copy()
    actual_y_sampled.index = pd.to_datetime(test_y.index)
    actual_y_sampled = actual_y_sampled.resample(f'{time_gap}').mean()
    
    mlp_pred_y_sampled.dropna(inplace=True)
    actual_y_sampled.dropna(inplace=True)
    
    mae = mean_absolute_error(y_true=actual_y_sampled,
                              y_pred=mlp_pred_y_sampled)
    r2 = r2_score(y_true=actual_y_sampled,
                  y_pred=mlp_pred_y_sampled)
    
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=actual_y_sampled.index, y=actual_y_sampled, name="Actual",
                             line_color='deepskyblue'))
    fig.add_trace(go.Scatter(x=mlp_pred_y_sampled.index, y=mlp_pred_y_sampled, name="Predicted",
                             line_color='dimgray'))
    fig.update_layout(title_text=f'MLP: {time_gap}: Actual vs Predicted, \tMAE: {mae:.3f}, \tR2: {r2:.3f}',
                      xaxis_rangeslider_visible=True)
    fig.show()